# cronIP - Versión 1.0
cronIP es un programa que se ejecuta desde crontab en SO Linux. Y su finalidad principal es informar del nombre del dispositivo y su IP de conexión. La información se envía actualizada cada 60 segundos al email de Gestión de dispositivos de Onwards.
## Novedades v0100 (18/02/18):
- El programa solo necesita una ejecución.
- Envío de fecha y hora del momento de ejecución del programa, y posteriormente en intervalos de 60 segundos.
- Envío de información respecto la temperatura de la CPU y la GPU del dispositivo.
- Envío del tiempo acumulado desde que se inició el programa (tiempo que lleva activo el dispositivo).

In [ ]:
#!/usr/bin/python
# -*- coding: utf-8 -*-

#########################################################################################################
 #    Autor:         Juan de Dios Yáñez Ávila    Email:           juandediosyanez@onw4rds.com
 #    Empresa:    Onwards                               Dirección:    www.onw4rds.com                                                                                                      
 #                                                                                                       
 #    cronIP es un programa que se ejecuta desde crontab en SO Linux. Y su finalidad principal es informar 
 #    del nombre del dispositivo y su IP de conexión. La información se envía actualizada cada 60 segundos 
 #    al email de Gestión de dispositivos de Onwards.
 #
 #    2018/02/17    Python 3    Versión 1.0    cronIP-v0100.py
 #    2017/12/30    Python 3    Versión 0.0    cronIP-v0000.py
#########################################################################################################


import smtplib, socket, commands, os
import datetime
import ftplib
import time
from email.mime.text import MIMEText
from io import open

# Tenemos que dar un tiempo al sistema para que se establezca conexión a red y no de error.
# Ya que necesitamos conocer la IP de conexión y si no tenemos conexión a internet tampoco
# iniciará el programa.
time.sleep(30)

#############
# Obtención de datos
eConexion = datetime.datetime.now()       # fecha de establecimiento de conexión
dispositivo = socket.gethostbyname()      # nombre del dispositivo
ip = commands.getoutput('hostname -I')    # IP del dispositivo
tTranscurrido = 0                         # tiempo transcurrido de conexión

#########
# Conocer temperatura de la CPU y la GPU
def get_cpu_temp():
    tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
    cpu_temp = tempFile.read()
    tempFile.close()
    cpu_temp = str(float(cpu_temp)/1000) +"ºC"
    return cpu_temp
    #Mostrar temperatura en grados Fahrenheit
    #return float(1.8*cpu_temp)+32

def get_gpu_temp():
    gpu_temp = commands.getoutput( "/opt/vc/bin/vcgencmd measure_temp" ).replace( 'temp=', '' ).replace( 'C', '' )
    gpu_temp = str(float(gpu_temp)) + "ºC"
    return gpu_temp
    #Mostrar temperatura en grados Fahrenheit
    # return float(1.8* gpu_temp)+32

########
# Enviar email con la información de la IP y de que todo marcha como debe
def email_ip():
    global eConexion
    global dispositivo
    global ip
    global iConexion
    global tTranscurrido

    direccion_ip = str(dispositivo) + " | " + str(ip)
    cpu_temp = get_cpu_temp()
    gpu_temp = get_gpu_temp()
    
    #SCRIPT PARA CREAR EL MENSAJE
    mensaje = MIMEText("""
                       Dispositivo:  {0}
                       IP:    {1}
                       Conexión establecida a las:  {2}
                       Temperatura de la CPU: {3}
                       Temperatura de la GPU: {4}
                       
                       Tiempo de funcionamiento aproximado: {5} segundos""" .format(dispositivo, ip, eConexion, cpu_temp, gpu_temp, tTranscurrido))
    mensaje['From'] = "onw4rds@gmail.com"
    mensaje['To'] = "onw4rds@gmail.com"
    mensaje['Subject'] = direccion_ip

    #SCRIPT PARA EL ENVIO DEL CORREO ELECTRONICO
    mailServer = smtplib.SMTP('smtp.gmail.com', 587)
    mailServer.ehlo()
    mailServer.starttls()
    mailServer.ehlo()
    mailServer.login("onw4rds@gmail.com", "#GOovh47536485q??")
    mailServer.sendmail("onw4rds@gmail.com", "onw4rds@gmail.com", mensaje.as_string())
    ## def sendmail(from_addr, to_addrs, msg, mail_options=[], rcpt_options=[])
    mailServer.quit()

while True:
    email_ip()
    time.sleep(60)
    ip = commands.getoutput('hostname -I')
    tTranscurrido = tTranscurrido + 60